# Анализ пространственных данных. Домашнее задание №2

Мягкий дедлайн: __4 ноября 2020 г. 23:59__

Жесткий дедлайн (со штрафом в _50%_ от количества набранных вами за ДЗ баллов): __5 ноября 2020 г. 08:59__

Визуализация "чего-либо" __без__ выполненного основного задания оценивается в __0 баллов__

ФИО: `Екатерина Касилина`

Группа: `MADE-DS-12`

## Задание №1. Горячая точка (алгоритм - 10 баллов, визуализация - 10 баллов).

Генерируйте рандомные точки на планете Земля до тех пор, пока не попадете на территорию ``Афганистана``

1. Вы можете использовать функции принадлжености точки полигону и расстояния от точки до полигона (в метрах)
2. Предложите не наивный алгоритм поиска (генерировать __напрямую__ точку из полигона границ Афганистана __запрещено__)

In [390]:
import requests
import json
import copy

from shapely.geometry import Point, LineString, Polygon
from shapely.ops import transform
import geopandas as gpd
import pandas as pd
from haversine import haversine
import numpy as np
from folium import plugins

In [52]:
import osmapi as osm
import folium

In [79]:
# Находим Афганистан
overpass_url = "http://overpass-api.de/api/interpreter"
overpass_query = """
[out:json];
relation["boundary"="administrative"]["admin_level"="2"]["name:UN:en"="Afghanistan"];
out geom;
"""
response = requests.get(overpass_url, 
                        params={'data': overpass_query})
data = response.json()

In [161]:
# Находим координаты
coords = []
for elem_1 in data['elements']:
    for elem_2 in elem_1['members']:
        if elem_2['type'] == 'way':
            for elem_3 in elem_2['geometry']:
                lon = elem_3['lon']
                lat = elem_3['lat']
                coords.append([lon, lat])

In [162]:
afganistan_polygon = Polygon(coords)

#### Алгоритм поиска:  
    1. Генериуем точку на из всех доступных координат на земле  
    2. Если точка не попала в полигон Афганистана берем ее в качестве минумума или максимума для следующего полигона в зависимости от расположения относительно центра полигона Афганистана
    3. Снова гененируем точку из получившегося полигона  

In [1465]:
# first point
lat_max, lat_min = 90.0000000, -90.0000000
lon_max, lon_min = 180.0000000, -180.0000000

points = []
polygons = []
for i in range(50):
    x, y = uniform(lat_min, lat_max), uniform(lon_min, lon_max)
    points.append([x, y])
    
    #(lat, lon)
    curr_dist = haversine((x, y), (afganistan_polygon.centroid.x, afganistan_polygon.centroid.y))
    print(f'Current distance from random point to Afganistan polygon centeroid {curr_dist}')
    rand_point = Point(x, y)
    if rand_point.within(afganistan_polygon):
        print('final point', x, y)
        fin_point = [x, y]
        fin_polygon = [[lat_min, lon_min],  [lat_max, lon_min], [lat_max, lon_max], [lat_min, lon_max]]
        break
    else:
        if x < afganistan_polygon.centroid.x:
            lat_min = x
        else:
            lat_max = x
     
        if y < afganistan_polygon.centroid.y:
            lon_min = y
        else:
            lon_max = y
            
        polygons.append([[lat_min, lon_min],  [lat_max, lon_min], [lat_max, lon_max], [lat_min, lon_max]])

Current distance from random point to Afganistan polygon centeroid 16578.75854607957
Current distance from random point to Afganistan polygon centeroid 9089.725518828265
Current distance from random point to Afganistan polygon centeroid 4358.230278207747
Current distance from random point to Afganistan polygon centeroid 1501.0267626896214
Current distance from random point to Afganistan polygon centeroid 530.0780825917216
final point 70.64641367026853 37.12725510895743


In [1466]:
search_polygon = []
for polygon in polygons:
    search_polygon.append(Polygon(polygon))

fin_polygon = Polygon(fin_polygon)

Визуализируйте пошагово предложенный алгоритм при помощи ``Folium``

In [1467]:
# Синий круг - сгенерированная точка, она же угол нового полигона
# финальный полигон и точка выделены красным
afganistan_map = folium.Map(location=[33.83472424, 66.0350383], zoom_start=1)
# Latitude and Longitude of Map
folium.GeoJson(afganistan_polygon).add_to(afganistan_map)

for poly in search_polygon:
    folium.GeoJson(poly, style_function=lambda feature: {
        'weight' : 0.2,
        'fillOpacity' : 0.1
        }).add_to(afganistan_map)
    
for poi in points:
    folium.CircleMarker(location=[poi[1], poi[0]]).add_to(afganistan_map)
    
folium.Marker(location=[points[0][1], points[0][0]], popup='Firts Point').add_to(afganistan_map)
    
folium.Marker(location=[fin_point[1], fin_point[0]], 
              icon=folium.Icon(color='red', icon='ok-sign'), popup='Final Point').add_to(afganistan_map)


folium.GeoJson(fin_polygon, style_function=lambda feature: {
        'weight' : 0.2,
        'fillOpacity' : 0.2,
        'fillColor' : 'red'
        }).add_to(afganistan_map)

afganistan_map

## Задание №2. Качество жизни (20 баллов).

Для измерения показателя качества жизни в точке, найденной в предыдущем задании, вам необходимо рассчитать следующую сумму расстояний (в метрах):

1. Расстояние от точки до 5 ближайших __*__ банкоматов, находящихся в стране с наибольшим количеством объектов жилой недвижимости
2. Расстояние от точки до 5 ближайших школ, находящихся в стране с наибольшим количеством аптек в столице
3. Расстояние от точки до 5 ближайших кинотеатров, наодящихся в стране с самым большим отношением числа железнодорожных станций к автобусным остановкам в южной части __**__

__*__ При поиске _N_ ближайших объектов обязательно использовать ``R-tree``

__**__ Южной частью страны является территория, находящаяся к югу от множества точек, равноудаленных от самой северной и самой южной точек страны

In [1160]:
## идея насчет стран принимается, только ограничимся теми, у которых areaId  в OSM заканчивается на 0
from OSMPythonTools.nominatim import Nominatim
from OSMPythonTools.overpass import overpassQueryBuilder, Overpass
from rtree import index

In [1047]:
overpass = Overpass()
result = overpass.query('relation["admin_level"="2"][boundary=administrative];out;')

In [505]:
## получаем названия всех стран
country_name = list()
for i in range(len(result.elements())):
    country_name.append(result.elements()[i].tag('name:en'))

In [507]:
nominatim = Nominatim()

In [515]:
countries_for_task = list()
for country in country_name:
    if country is not None:
        areaId = nominatim.query(country).areaId()
        if (str(areaId)[-1]) == '0':
            countries_for_task.append([country, areaId])

##### 1. Расстояние от точки до 5 ближайших банкоматов, находящихся в стране с наибольшим количеством объектов жилой недвижимости

In [1541]:
# наибольшим количеством объектов жилой недвижимости
accommodation_list = ['apartments', 'bungalow', 'cabin', 'detached', 'dormitory', 'farm', 'ger', 'hotel', 
'house', 'houseboat', 'residential', 'semidetached_house', 'static_caravan', 'terrace']

resulted_list_acc = list()

for country in countries_for_task:
    accommodation_cnt = 0
    
    for building in accommodation_list:
        query = overpassQueryBuilder(area=country[1], elementType=['node', 'way', 'relation'], 
                                     selector=f'"building"= {building}', out='count')
        result = overpass.query(query, timeout=180)
        cnt = result.countElements()
        accommodation_cnt += cnt
    resulted_list_acc.append([country[0], accommodation_cnt])

In [1562]:
resulted_list_acc

[['Brazil', 759937],
 ['Estonia', 9324],
 ['Australia', 588866],
 ['Eswatini', 7287],
 ['Bangladesh', 50825],
 ['Syria', 13627],
 ['Liberia', 52614],
 ['Central African Republic', 7913],
 ['Ethiopia', 11047],
 ['Cameroon', 22088],
 ['Tanzania', 296201],
 ['Malawi', 97672],
 ['Uzbekistan', 42906],
 ['Honduras', 33011],
 ['Portugal', 271551],
 ['Azerbaijan', 22089],
 ['Comoros', 8286],
 ['São Tomé and Príncipe', 110],
 ['Antigua and Barbuda', 438],
 ['Monaco', 55],
 ['Kosovo', 24170],
 ['Brunei', 15044],
 ['Tokelau', 1],
 ['Norway', 322976]]

In [1546]:
# Наибольшее количество объектов недвижимости находится в этой стране
sorted(resulted_list_acc, key = lambda x: x[1])[-1]

['Brazil', 759937]

In [1552]:
# Brazil atm
query = overpassQueryBuilder(area=3600059470, elementType=['node', 'relation'], 
                                     selector='"amenity" = "atm"')
result_atm = overpass.query(query, timeout=180)

[overpass] downloading data: [timeout:180][out:json];area(3600059470)->.searchArea;(node["amenity" = "atm"](area.searchArea);relation["amenity" = "atm"](area.searchArea);); out body;


In [1549]:
final_point = list(reversed(fin_point))

In [1550]:
def get_distance(geo_data, point):
    
    point_in_afganistan = copy.deepcopy(point)
    point_in_afganistan_2 = copy.deepcopy(point)  
    
    all_points = []
    for i in geo_data.elements():
        all_points.append(i.geometry()['coordinates'])
        

    all_points_reversed = copy.deepcopy([elem[::-1] for elem in all_points])
    all_points_rever_copy = copy.deepcopy(all_points_reversed)
    
    # build index
    idx_rtree = index.Rtree()
    for i, p in enumerate(all_points_rever_copy):
        idx_rtree.insert(i, p)
        
    # find the nearest points 
    nearest_points = []
    nearest_obj = list(idx_rtree.nearest(point_in_afganistan, 5))
    nearest_points = [all_points_reversed[i] for i in nearest_obj]

    ## find distance
    dist = []
    for i in nearest_points:
        #(lat, lon) # in kilometers
        dist.append(haversine(i, point_in_afganistan_2))
    
    return dist

In [1553]:
atm_dist = get_distance(result_atm, final_point)

In [1554]:
print(f"Mean distance to the closest atms is {np.round(np.mean(atm_dist), 2)} km.")
print("Exact distance in km: ")
print(' '.join(str(num) + '\n' for num in atm_dist))

Mean distance to the closest atms is 11423.2 km.
Exact distance in km: 
11421.749613919452
 11421.81017945725
 11423.658229683966
 11424.377913697565
 11424.380310335871



##### 2. Расстояние от точки до 5 ближайших школ, находящихся в стране с наибольшим количеством аптек в столице

In [1074]:
## находим имена столиц для каждой страны
capitals = []
for country in countries_for_task:
    query = overpassQueryBuilder(area=country[1], elementType=['node'], 
                                     selector="capital = yes")
    result = overpass.query(query, timeout=180)
    cap = ''
    areaId = 0
    if len(result.toJSON()['elements']) > 0 :
        cap = result.toJSON()['elements'][0]['tags']['name:en']
        areaId = nominatim.query(cap).areaId()
    capitals.append([country[0], cap, areaId])

In [1129]:
# столица Австралии
capitals[2][1] = 'Australian Capital Territory'
capitals[2][2] = nominatim.query('Australian Capital Territory').areaId() 

[nominatim] downloading data: Australian Capital Territory


In [1537]:
pharmacy_list = []
for cap in capitals:
    if cap[2] is not None and cap[2] != 0 :
        query = overpassQueryBuilder(area=cap[2], elementType=['node', 'way', 'relation'], 
                                     selector='"amenity"="pharmacy"', out='count')
        result = overpass.query(query, timeout=180)
        cnt = result.countElements()
        pharmacy_list.append([cap[0], cap[1], cnt])

In [1538]:
## Столица Бразилии не ищется через areaId, т.к этот id совпадает с id самой страны
# поэтому смотрим кол-во аптек через bbox
query = overpassQueryBuilder(bbox=[-15.95, -47.72, -15.63,  -48.04], 
                                     elementType=['node', 'way', 'relation'], 
                                     selector='"amenity"="pharmacy"', out='count')
result = overpass.query(query, timeout=180)
pharmacy_list[0][2] = result.countElements()

In [1555]:
# стране с наибольшим количеством аптек в столице
sorted(pharmacy_list, key = lambda x: x[2])[-1]

['Uzbekistan', 'Tashkent', 853]

In [1559]:
query = overpassQueryBuilder(area=3600196240, elementType=['node'], 
                                     selector='"amenity" = "school"')
result_school = overpass.query(query, timeout=180)

[overpass] downloading data: [timeout:180][out:json];area(3600196240)->.searchArea;(node["amenity" = "school"](area.searchArea);); out body;


In [1560]:
school_dist = get_distance(result_school, final_point)

In [1561]:
print(f"Mean distance to the 5 closest schools is {np.round(np.mean(school_dist), 2)} km.")
print("Exact distance in km: ")
print(' '.join(str(num) + '\n' for num in school_dist))

Mean distance to the 5 closest schools is 300.37 km.
Exact distance in km: 
316.2696410878377
 316.28123139355733
 316.5991070161781
 272.8010756788196
 279.8919492129323



##### 3. Расстояние от точки до 5 ближайших кинотеатров, наодящихся в стране с самым большим отношением числа железнодорожных станций к автобусным остановкам в южной части 

In [ ]:
## не успеваю

## Задание №3. Поездка по Нью-Йорку (маршрут - 20 баллов, визуализация - 10 баллов).

Добраться __на автомобиле__ от входа в ``Central Park`` __Нью-Йорка__ (со стороны ``5th Avenue``) до пересечения ``Water Street`` и ``Washington Street`` в Бруклине (откуда получаются лучшие фото Манхэттенского моста) довольно непросто - разумеется, из-за вечных пробок. Однако еще сложнее это сделать, проезжая мимо школ, где дети то и дело переходят дорогу в неположенном месте.

Вам необходимо построить описанный выше маршрут, избегая на своем пути школы. Визуализируйте данный маршрут (также добавив школы и недоступные для проезда участки дорог) при помощи ``Folium``

Данные о расположении школ Нью-Йорка можно найти [здесь](https://catalog.data.gov/dataset/2019-2020-school-point-locations)

In [983]:
from openrouteservice import client
import pyproj
from shapely import geometry
from shapely.geometry import Point, LineString, Polygon, MultiPolygon

In [1017]:
school_data = pd.read_csv('2019_-_2020_School_Point_Locations.csv')

In [1018]:
# плучим координаты школ
points_list = []
for idx, row  in school_data.iterrows():
    points_list.append([float(row.loc['geometry'].split()[1][1:]), float(row.loc['geometry'].split()[2][:-1])])

In [1019]:
# ограниичим выборку по школам вероятным маршрутом: Квинс, Бруклин Манхеттен
points_list = [i for i in points_list if i[0] < -73.90 and i[1] > 40.68]

In [921]:
api_key = '' #https://openrouteservice.org/sign-up
clnt = client.Client(key=api_key)

In [1015]:
central_park_point = [-73.958562, 40.784074]
finish_point = [-73.989599, 40.703247]

coordinates = [central_park_point, finish_point]

def style_function(color):
    return lambda feature: dict(color=color,
                              weight=5,
                              opacity=0.5)

In [1021]:
# вспомогательная функция для расчета полигона вокруг школ
def CreateBufferPolygon(point_in, resolution=10, radius= 300):    

    sr_wgs = pyproj.Proj(init='epsg:4326')
    sr_utm = pyproj.Proj(init='epsg:32632') # WGS84 UTM32N
    point_in_proj = pyproj.transform(sr_wgs, sr_utm, *point_in) # unpack list to arguments
    point_buffer_proj = Point(point_in_proj).buffer(radius, resolution=resolution) # 10 m buffer
    
    # Iterate over all points in buffer and build polygon
    poly_wgs = []
    for point in point_buffer_proj.exterior.coords:
        poly_wgs.append(pyproj.transform(sr_utm, sr_wgs, *point)) # Transform back to WGS84

    return poly_wgs

In [1025]:
# считаем что полигон с радиусом 150 м вокруг школы - заблокированная область для проезда
# посчитаем полигоны и нанесем их на карту
# Если полигон пересекает дорогу - эта дорога не доступна для проезда
nyc_map = folium.Map(location=[40.78598, -73.95718], zoom_start=12)

school_poly = []
for school_data in points_list:
    folium.features.Marker(list(reversed(school_data))).add_to(nyc_map)
    
    # Create buffer polygons around construction sites with 10 m radius and low resolution
    school_poly_coords = CreateBufferPolygon(school_data,
                                           resolution=2, # low resolution to keep polygons lean
                                           radius=150)
    school_poly.append(school_poly_coords)
    
    site_poly_coords_tmp = [(y,x) for x,y in school_poly_coords] # Reverse coords for folium/Leaflet
    folium.vector_layers.Polygon(locations=site_poly_coords_tmp,
                                  color='#de4e77',
                                  fill_color='#de4e77',
                                  fill_opacity=0.2,
                                  weight=3).add_to(nyc_map)

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

...

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  return _prepare_from_string(" ".join(pjargs))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:294: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  projstring = _prepare_from_string(" ".join((projstring, projkwargs)))
/Users/ekaterina/opt/anaconda3/envs/geo/lib/python3.7/site-packages/pyproj/crs/crs.py:53: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<c

In [1026]:
# Строим маршрут в объезд посчитанных полигонов
# Детали маршрута описаны после карты
coordinates = [central_park_point, finish_point]
direction_params = {'coordinates': coordinates,
                    'profile': 'driving-car', 
                    'format_out': 'geojson',
                    'preference': 'shortest',
                    'geometry': 'true',
                    'instructions': 'true'}

regular_route = clnt.directions(**direction_params)

school_buffer_poly = []
for site_poly in school_poly:
    poly = Polygon(site_poly)
    school_buffer_poly.append(poly)

direction_params['options'] = {'avoid_polygons': geometry.mapping(MultiPolygon(school_buffer_poly))}
route_detour = clnt.directions(**direction_params)

folium.features.GeoJson(data=route_detour,
                        name='Detour Route',
                        style_function=style_function('#3bd440'),
                        overlay=True).add_to(nyc_map)

nyc_map.add_child(folium.map.LayerControl())
nyc_map

In [1037]:
distance, duration = route_detour['features'][0]['properties']['summary'].values()
route_details = []
for inst in route_detour['features'][0]['properties']['segments']:
    for i, elem in enumerate(inst['steps']):
        route_details.append(str(i)+' '+elem['instruction'])
        

In [1046]:
## Детали маршрута
print('Your route details are here!')
print(f'Distance: {np.round(distance/1000)} km., duration: {np.round(duration/60)} mins.')
print('')
print('Please, follow this instructions:')
print(' '.join(str(num) + '\n' for num in route_details))

Your route details are here!
Distance: 16.0 km., duration: 31.0 mins.

Please, follow this instructions:
0 Head southwest on 5th Avenue
 1 Turn left onto East 74th Street
 2 Turn right onto Lexington Avenue
 3 Turn left onto East 59th Street
 4 Turn right onto 2nd Avenue
 5 Turn left onto East 58th Street
 6 Keep left
 7 Keep right
 8 Turn left onto 21st Street
 9 Turn left onto 43rd Avenue
 10 Turn right onto 23rd Street
 11 Turn right onto Jackson Avenue, NY 25A
 12 Continue straight onto Jackson Avenue
 13 Keep left onto Pulaski Bridge
 14 Turn right onto Meserole Avenue
 15 Turn left onto Leonard Street
 16 Turn right onto Driggs Avenue
 17 Turn left onto Lorimer Street
 18 Turn right onto Meeker Avenue
 19 Turn right onto Metropolitan Avenue
 20 Turn left onto Marcy Avenue
 21 Keep left
 22 Keep right
 23 Turn right onto Flushing Avenue
 24 Turn right
 25 Turn right
 26 Turn left onto Sands Street
 27 Turn slight right onto Sands Street
 28 Turn sharp right onto Gold Street
 29 Tu